# Final analysis

This notebook contains the final form of our analysis as well as the final form of the data cleaning process.

In [ ]:
import glob
import os
import pandas as pd
path = r'/home/daniel/code/costofcare/data/bhp_ukhls_data_stata/UKDA-6614-stata/stata/ukhls'
all_files = glob.glob(os.path.join(path , '*indresp.dta'))
raw_colnames = ['hidp',
                'sex',
                'jbnssec_dv',
                'jbnssec8_dv',
                'jbstat',
                'jbhrs',
                'ethn_dv',
                'dvage',
                'mastat_dv',
                'country',
                'aidhh',
                'aidhrs',
                'aidxhh',
                'paygu_dv',
                'qfhigh',
                'qfhigh_dv',
                'istrtdatm',
                'istrtdaty',
                'month']
indresp = []
prefixes = [] # for later
for filename in all_files:
    prefix = filename.split('/')[-1][0:2]
    prefixes.append(prefix)
    colnames = [f'{prefix}{x}' for x in raw_colnames]
    temp_df = pd.read_stata(filename,
                       columns=['pidp'] + colnames)
    indresp.append(temp_df)

In [ ]:
for i, df in enumerate(indresp):
    df['wave'] = i+1
    df.columns = ['pidp',
                'hidp',
                'sex',
                'jbnssec_dv',
                  'jbnssec8_dv',
                'jbstat',
                'jbhrs',
                'ethn_dv',
                'dvage',
                'mastat_dv',
                'country',
                'aidhh',
                'aidhrs',
                'aidxhh',
                'paygu_dv',
                'qfhigh',
                'qfhigh_dv',
                'istrtdatm',
                'istrtdaty',
                'month',
                 'wave']

In [ ]:
data = pd.concat(indresp)
data['max_waves'] = data.groupby('pidp')['wave'].transform('count')
len(data.pidp.unique())

In [ ]:
check = data[['wave', 'pidp', 'max_waves']]

In [ ]:
len(check[check.max_waves > 5].pidp.unique())

## Decision
We will consider that has at least six data points, whether or not they are consecutive or not, and whether or not they start from wave 1.

In [ ]:
data_6 = data[data.max_waves > 5]
len(data_6.pidp.unique())

# Treatment Variable

## Decision
Recoding treatment variable

In [ ]:
import numpy as np
data_6['aidhh_recoded'] = data_6.aidhh.replace({'Yes': 'yes',
                                                'No': 'no',
                                                'no     ': 'no',
                                                'yes    ': 'yes',
                                                'Not available for IEMB': np.nan,
                                                "don't know": np.nan,
                                                'proxy': np.nan,
                                                'missing': np.nan,
                                                'refusal': np.nan,
                                                'inapplicable': np.nan})

In [ ]:
data_6['aidxhh_recoded'] = data_6.aidxhh.replace({'Yes': 'yes',
                                                'No': 'no',
                                                'no     ': 'no',
                                                'yes    ': 'yes',
                                                'Not available for IEMB': np.nan,
                                                "don't know": np.nan,
                                                'proxy': np.nan,
                                                'missing': np.nan,
                                                'refusal': np.nan,
                                                'inapplicable': np.nan})

In [ ]:
data_6['aidhrs_recoded_3'] = data_6.aidhrs.str.strip().replace({"inapplicable": np.nan,
                                   "0 - 4 hours per week": "0-19",
                                   "proxy": np.nan,
                                   "5 - 9 hours per week": "0-19",
                                   "10 - 19 hours per week": "0-19",
                                   "100 or more hours per week/continuous care": "50+",
                                   "20 - 34 hours per week": "20-49",
                                   "35 - 49 hours per week": "20-49",
                                   "varies 20 hours or more": "20-49",
                                   "0 - 4 hours per week": "0-19",
                                   "10-19 hours per week": "0-19",
                                   "Not available for IEMB": np.nan,
                                   "Varies 20 hours or more": "20-49",
                                   "varies under 20 hours": "0-19",
                                   "Varies under 20 hours": "0-19",
                                   "20-34 hours per week": "20-49",
                                   "5 - 9 hours per week": "0-19",
                                   "Other": np.nan,
                                   "10 - 19 hours per week": "0-19",
                                   "35-49 hours per week": "20-49",
                                   "100 or more hours per week/continuous care": "50+",
                                   "20 - 34 hours per week": "20-49",
                                   "50-99 hours per week": "50+",
                                   "other": np.nan,
                                   "don't know": np.nan,
                                   "35 - 49 hours per week": "20-49",
                                   "varies under 20 hours": "0-19",
                                   "50 - 99 hours per week": "50+",
                                   "other": np.nan,
                                   "refusal": np.nan}).copy()

## Note
The variable below identifies the people who provided care under our specific conditions based on the 3 variables above.

In [ ]:
data_6['carer'] = ((data_6.aidhh_recoded == 'yes') | (data_6.aidxhh_recoded == 'yes') | (~data_6.aidhrs_recoded_3.isnull()))

Counting how many waves are carers taking care responsabilities on average

In [ ]:
care_resp = data_6[['pidp', 'carer', 'wave']][data_6.carer]
care_resp['max_waves'] = care_resp.groupby('pidp')['wave'].transform('count')
care_resp.drop_duplicates(subset=['pidp']).max_waves.mean()

## Decision
We will use a "generalised" moment of treatment with at least 3 measures before, and at least 1 after.

# Target Variable

In [ ]:
data_6['jbstat_clean'] = data_6.jbstat.str.strip().str.lower() # cleaning values here

In [ ]:
data_6.jbstat_clean.value_counts()

In [ ]:
data_6['employed'] = data_6.jbstat_clean.replace({"paid employment(ft/pt)": "employed",
                             "retired": "unemployed",
                       "self employed": "employed",
                       "family care or home": "unemployed",
                       "unemployed": "unemployed",
                       "full-time student": "unemployed",
                       "lt sick or disabled": "unemployed",
                       "on maternity leave": "employed",
                       "doing something else": "unemployed",
                       "on furlough": "unemployed",
                       "on apprenticeship": "employed",
                       "unpaid, family business": "unemployed",
                       "govt training scheme": "employed",
                       "refusal": np.nan,
                       "temporarily laid off/short term working": "unemployed",
                       "don't know": np.nan,
                       "missing": np.nan}
                     )

Total Sample size

In [143]:
data_6[['pidp', 'carer']].drop_duplicates(subset=['pidp'])

pidp  carer
1        68004087  False
2        68006127  False
4        68006807  False
11       68008847  False
12       68009527  False
...           ...    ...
41859  1636671692   True
41873  1638419292   True
41930  1644675490  False
41931  1644675530  False
41933  1644736490  False

[40123 rows x 2 columns]

Total number of carers in sample

In [144]:
data_6[['pidp', 'carer']].drop_duplicates(subset=['pidp'])['carer'].sum()

6529

Number of employed individuals in the sample

In [145]:
len(data_6[(data_6.employed == 'employed')].drop_duplicates(subset=['pidp']))

29337

Number of employed carers

In [146]:
data_6[(data_6.employed == 'employed')].drop_duplicates(subset=['pidp']).carer.sum()

4340

## Decision
We are considering only employed individuals

In [147]:
df_6_emp = data_6[(data_6.employed == 'employed')]

Cleaning wage variable

In [148]:
df_6_emp['wage'] = df_6_emp.paygu_dv.replace({'inapplicable': np.nan, 'proxy': np.nan, 'missing': np.nan})

/tmp/ipykernel_5690/3065558054.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_6_emp['wage'] = df_6_emp.paygu_dv.replace({'inapplicable': np.nan, 'proxy': np.nan, 'missing': np.nan})


In [149]:
df_6_emp.wage

1        1075.000000
11       1282.170044
12       4116.669922
14       2333.330078
16       2641.449951
            ...     
29258    4583.330078
29259    7000.000000
29260    1624.750000
29263    2800.000000
29267            NaN
Name: wage, Length: 221411, dtype: float64

Adding cpih to correct for inflation

In [150]:
cpih = pd.read_csv('./cpih_uk_88_23.csv')
cpih['date'] = pd.to_datetime(cpih.date, format='%b-%y')
cpih

date   cpih
0   1988-01-01   46.9
1   1988-02-01   47.0
2   1988-03-01   47.2
3   1988-04-01   47.8
4   1988-05-01   48.0
..         ...    ...
416 2022-09-01  122.3
417 2022-10-01  124.3
418 2022-11-01  124.8
419 2022-12-01  125.3
420 2023-01-01  124.8

[421 rows x 2 columns]

In [151]:
df_6_emp['istrtdaty'] = df_6_emp['istrtdaty'].astype('str').replace({'inapplicable': np.nan, 'missing': np.nan, "don't know": np.nan})
df_6_emp['istrtdatm'] = df_6_emp['istrtdatm'].replace({'inapplicable': np.nan, 'missing': np.nan, "don't know": np.nan})
df_6_emp['date'] = df_6_emp['istrtdaty'].astype(str) + '/' + df_6_emp['istrtdatm'].astype(str)
df_6_emp['date'] = df_6_emp['date'].replace({'nan/nan': np.nan})
df_6_emp['date'] = pd.to_datetime(df_6_emp['date'], format='%Y/%B')
df_6_emp = df_6_emp.merge(cpih, on='date', how='left')

/tmp/ipykernel_5690/1591602359.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_6_emp['istrtdaty'] = df_6_emp['istrtdaty'].astype('str').replace({'inapplicable': np.nan, 'missing': np.nan, "don't know": np.nan})
/tmp/ipykernel_5690/1591602359.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_6_emp['istrtdatm'] = df_6_emp['istrtdatm'].replace({'inapplicable': np.nan, 'missing': np.nan, "don't know": np.nan})
/tmp/ipykernel_5690/1591602359.py:3: SettingWithCopyWarning: 
A value is trying to be set 

In [152]:
df_6_emp['jbhrs_clean'] = df_6_emp.jbhrs.replace({'inapplicable': np.nan, 'proxy': np.nan, 'missing': np.nan, "don't know": np.nan, "refusal": np.nan, 0: np.nan})
df_6_emp['jbhrs_clean'][df_6_emp.jbhrs_clean < 1] = np.nan

/tmp/ipykernel_5690/295635728.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_6_emp['jbhrs_clean'][df_6_emp.jbhrs_clean < 1] = np.nan


In [153]:
df_6_emp['month_jbhrs'] = df_6_emp['jbhrs_clean'] * 4.33 # times the average amount of weeks

In [154]:
df_6_emp['wage_h'] = df_6_emp['wage'] / df_6_emp['month_jbhrs']

### Real wage calculation

In [155]:
df_6_emp['wage_h_deflated'] = (df_6_emp['wage_h'] / df_6_emp['cpih']) * 100

# ISC Data preparation

In [156]:
isc_data = df_6_emp[['pidp', 'carer', 'wage_h_deflated', 'wave', 'date']]

In [157]:
isc_data

pidp  carer  wage_h_deflated  wave       date
0         68004087  False         7.350859     1 2009-01-01
1         68008847  False         8.767489     1 2009-01-01
2         68009527  False        29.671434     1 2009-01-01
3         68010887  False        16.817780     1 2009-01-01
4         68011567  False        19.038594     1 2009-01-01
...            ...    ...              ...   ...        ...
221406  1652366050  False        24.790524    12 2022-02-01
221407  1652814850   True        35.421301    12 2021-11-01
221408  1652835250  False         8.888148    12 2021-11-01
221409  1652984930  False        15.036391    12 2021-12-01
221410  1653134490  False              NaN    12 2021-12-01

[221411 rows x 5 columns]

### Average number of waves caring

In [158]:
carer_events = []
for i in isc_data.pidp.unique():
    by_pidp = isc_data[isc_data.pidp == i]
    if by_pidp.carer.any():
        carer_events.append(by_pidp.carer.sum())
np.mean(carer_events)

3.041845399632321

## Decision
We will take the average as lower limit to determine treated cases. Everyone with less than 3 and more than 1 reported waves of caring will be dropped.

In [159]:
isc_data['waves_caring'] = isc_data.groupby('pidp')['carer'].transform('sum')
isc_data = isc_data[~((isc_data.waves_caring >= 1) & (isc_data.waves_caring < 3))]

/tmp/ipykernel_5690/2949276746.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  isc_data['waves_caring'] = isc_data.groupby('pidp')['carer'].transform('sum')


In [160]:
isc_data['wave_reindex'] = isc_data.sort_values(by=['pidp', 'wave']).groupby('pidp').cumcount() + 1

/tmp/ipykernel_5690/1634805651.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  isc_data['wave_reindex'] = isc_data.sort_values(by=['pidp', 'wave']).groupby('pidp').cumcount() + 1


In [161]:
for i in isc_data.pidp.unique():
    by_pidp = isc_data[isc_data.pidp == i]
    if by_pidp.carer.any():
        by_pidp['wave_treated'] = by_pidp['carer'].idxmax()
        print(by_pidp)

/tmp/ipykernel_5690/2579416863.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  by_pidp['wave_treated'] = by_pidp['carer'].idxmax()
/tmp/ipykernel_5690/2579416863.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  by_pidp['wave_treated'] = by_pidp['carer'].idxmax()
/tmp/ipykernel_5690/2579416863.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pyd

            pidp  carer  wage_h_deflated  wave       date  waves_caring  \
5       68028571  False        15.616555     1 2009-01-01             3   
14993   68028571   True        15.639664     2 2010-01-01             3   
54218   68028571   True        14.389492     4 2012-02-01             3   
94884   68028571  False        14.361609     6 2014-04-01             3   
136507  68028571   True         6.873419     8 2016-05-01             3   
156022  68028571  False        10.202955     9 2017-08-01             3   

        wave_reindex  wave_treated  
5                  1         14993  
14993              2         14993  
54218              3         14993  
94884              4         14993  
136507             5         14993  
156022             6         14993  
            pidp  carer  wage_h_deflated  wave       date  waves_caring  \
14      68043527  False        13.229050     1 2009-03-01             5   
54227   68043527   True        16.030099     4 2012-01-01        

/tmp/ipykernel_5690/2579416863.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  by_pidp['wave_treated'] = by_pidp['carer'].idxmax()
/tmp/ipykernel_5690/2579416863.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  by_pidp['wave_treated'] = by_pidp['carer'].idxmax()
/tmp/ipykernel_5690/2579416863.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pyd

            pidp  carer  wage_h_deflated  wave       date  waves_caring  \
445     69074411   True        22.667997     1 2009-01-01            12   
15461   69074411   True        72.821089     2 2010-01-01            12   
34920   69074411   True        45.611852     3 2011-02-01            12   
54684   69074411   True         5.434044     4 2012-02-01            12   
74893   69074411   True         9.904526     5 2013-01-01            12   
95355   69074411   True        34.886236     6 2014-03-01            12   
116396  69074411   True        23.187438     7 2015-03-01            12   
136943  69074411   True        12.220172     8 2016-03-01            12   
156423  69074411   True        11.276703     9 2017-02-01            12   
174557  69074411   True        14.190354    10 2018-02-01            12   
191732  69074411   True        19.281972    11 2019-04-01            12   
207563  69074411   True        10.645008    12 2020-02-01            12   

        wave_reindex  wa

/tmp/ipykernel_5690/2579416863.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  by_pidp['wave_treated'] = by_pidp['carer'].idxmax()
/tmp/ipykernel_5690/2579416863.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  by_pidp['wave_treated'] = by_pidp['carer'].idxmax()
/tmp/ipykernel_5690/2579416863.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pyd

...

              pidp  carer  wage_h_deflated  wave       date  waves_caring  \
113729  1441246450  False        14.324108     6 2015-10-01             6   
134378  1441246450   True        12.952368     7 2016-08-01             6   
153954  1441246450   True        13.165845     8 2017-09-01             6   
172249  1441246450   True        15.628958     9 2018-08-01             6   
189511  1441246450   True        16.811962    10 2019-07-01             6   
205603  1441246450   True        12.621302    11 2020-08-01             6   
219997  1441246450   True        17.556233    12 2021-07-01             6   

        wave_reindex  wave_treated  
113729             1        134378  
134378             2        134378  
153954             3        134378  
172249             4        134378  
189511             5        134378  
205603             6        134378  
219997             7        134378  
              pidp  carer  wage_h_deflated  wave       date  waves_caring  \
113990  14

/tmp/ipykernel_5690/2579416863.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  by_pidp['wave_treated'] = by_pidp['carer'].idxmax()
/tmp/ipykernel_5690/2579416863.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  by_pidp['wave_treated'] = by_pidp['carer'].idxmax()
/tmp/ipykernel_5690/2579416863.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pyd

             pidp  carer  wage_h_deflated  wave       date  waves_caring  \
128707  884755487  False              NaN     7 2016-02-01             3   
148637  884755487  False              NaN     8 2017-03-01             3   
167311  884755487   True              NaN     9 2018-02-01             3   
184731  884755487   True              NaN    10 2019-02-01             3   
201350  884755487   True              NaN    11 2020-02-01             3   
216274  884755487  False              NaN    12 2021-02-01             3   

        wave_reindex  wave_treated  
128707             1        167311  
148637             2        167311  
167311             3        167311  
184731             4        167311  
201350             5        167311  
216274             6        167311  
              pidp  carer  wage_h_deflated  wave       date  waves_caring  \
130427  1030601290  False              NaN     7 2016-01-01             3   
150225  1030601290  False              NaN     8 2017-

/tmp/ipykernel_5690/2579416863.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  by_pidp['wave_treated'] = by_pidp['carer'].idxmax()
/tmp/ipykernel_5690/2579416863.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  by_pidp['wave_treated'] = by_pidp['carer'].idxmax()
/tmp/ipykernel_5690/2579416863.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pyd

             pidp  carer  wage_h_deflated  wave       date  waves_caring  \
156914  136025175   True         4.642224     9 2017-02-01             3   
175024  136025175   True         4.144391    10 2018-01-01             3   
192154  136025175   True         7.616706    11 2019-02-01             3   

        wave_reindex  wave_treated  
156914             1        156914  
175024             2        156914  
192154             3        156914  
             pidp  carer  wage_h_deflated  wave       date  waves_caring  \
157908  204166615   True         3.878953     9 2017-04-01             4   
175935  204166615   True         3.161990    10 2018-04-01             4   
193015  204166615   True         4.328345    11 2019-06-01             4   
208794  204166615   True         3.547897    12 2020-06-01             4   

        wave_reindex  wave_treated  
157908             1        157908  
175935             2        157908  
193015             3        157908  
208794            